# Cast civitai trained LoRa in torch.bfloat16 to Tensor Art Compatible torch.float16 dtype

Created by Adcom: https://tensor.art/u/743241123023077878

In [1]:
#initialize
import torch
from safetensors.torch import load_file, save_file
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [19]:
import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# This method rescales a _lora to a given ratio. I haven't tested it
# yet but this is more or less how it works
def rescale_and_save(_lora , savefile_name, new_ratio , rank):
    count = 0
    lora = {}
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    decimals = 6
    for key in _lora:
        if not f'{key}'.find('alpha') > -1: continue
        alpha = f'{key}'
        up = f'{key}'.replace('alpha' , 'lora_up.weight')
        down = f'{key}'.replace('alpha' , 'lora_down.weight')
        #------#
        new_alpha = torch.tensor(new_ratio*rank).to(device = device , dtype=torch.float32)
        lora[up] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[up], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[down], decimals = decimals).to(device = device , dtype=torch.float32)
        #-----#
        lora[alpha] = (new_alpha/_lora[alpha])*_lora[alpha].to(device = device , dtype=torch.float32)
        count = count + 3
        print(f'{count} / {NUM_ITEMS}')
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
  #-----------#

tgt = load_file('/content/drive/MyDrive/Saved from Chrome/window-voyeur- F.safetensors')
for key in tgt:
  if f'{key}'.find('alpha')>-1: print(tgt[f'{key}'])
  print(f" {key} : {tgt[f'{key}'].shape}")

name = 'window'
savefile_name = f'{name}.safetensors'
new_ratio = 0.5
rank = 4

rescale_and_save(tgt , savefile_name, new_ratio , rank)
  #(alpha/scale) = (32/16)



tensor(1., dtype=torch.bfloat16)
 lora_te1_text_model_encoder_layers_0_mlp_fc1.alpha : torch.Size([])
 lora_te1_text_model_encoder_layers_0_mlp_fc1.lora_down.weight : torch.Size([4, 768])
 lora_te1_text_model_encoder_layers_0_mlp_fc1.lora_up.weight : torch.Size([3072, 4])
tensor(1., dtype=torch.bfloat16)
 lora_te1_text_model_encoder_layers_0_mlp_fc2.alpha : torch.Size([])
 lora_te1_text_model_encoder_layers_0_mlp_fc2.lora_down.weight : torch.Size([4, 3072])
 lora_te1_text_model_encoder_layers_0_mlp_fc2.lora_up.weight : torch.Size([768, 4])
tensor(1., dtype=torch.bfloat16)
 lora_te1_text_model_encoder_layers_0_self_attn_k_proj.alpha : torch.Size([])
 lora_te1_text_model_encoder_layers_0_self_attn_k_proj.lora_down.weight : torch.Size([4, 768])
 lora_te1_text_model_encoder_layers_0_self_attn_k_proj.lora_up.weight : torch.Size([768, 4])
tensor(1., dtype=torch.bfloat16)
 lora_te1_text_model_encoder_layers_0_self_attn_out_proj.alpha : torch.Size([])
 lora_te1_text_model_encoder_layers_0_self

In [14]:
tgt = load_file('/content/doggy.safetensors')
for key in tgt:
  if f'{key}'.find('alpha')>-1: print(tgt[f'{key}'])
  print(tgt[f'{key}'].shape)

tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([3072, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 3072])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([3072, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 3072])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.Size([768, 32])
tensor(16., dtype=torch.float16)
torch.Size([])
torch.Size([32, 768])
torch.

In [ ]:

import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# For pcnt = 30 , 'filter_and_save'  will keep all top 30 % values
#, and the lowest (negative) 30% values for each layer delta_W in this lora
# Then save the new filtered lora as a .safetensor file
def filter_and_save(_lora , savefile_name, new_rank , new_alpha, resolution):
    lora = {}
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = resolution*0.000001 # 1e-6
    #-------#
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        #---#
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.zeros(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 1
        y[indices[values<-thresh]] = 1
        y = y.unflatten(0,delta_W.shape).to(device = device , dtype=torch.float32)
        delta_W = torch.mul(delta_W,y).to(device = device , dtype=torch.float32)
        #------#
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        #-------#
        tmp['u'] = torch.round(torch.matmul(tmp['u'], torch.diag(tmp['s'])),decimals=6)
        tmp['Vh'] = torch.round(tmp['Vh'].t()[: new_rank,:],decimals=6)
        #-------#
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = tmp['u'].to(device = device , dtype=torch.float32)
        lora[down] = tmp['Vh'].to(device = device , dtype=torch.float32)
        #-------#
        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}')
    #-------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in _lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#--------#

def count_zeros(_lora, resolution):
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    #-----#
    thresh = resolution*0.000001 # 1e-6

    print(f'at resolution = {resolution}e-6 :')
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            count = count + 1
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.ones(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 0
        neg_pcnt  = round((100*torch.sum(y) / N).item(),2)
        y[indices[values<-thresh]] = 0
        count  = count  + 2
        pcnt  = round((100*torch.sum(y) / N).item(),2)
        neg_pcnt = round(neg_pcnt - pcnt,2) # remove zero % from neg_pcnt
        pos_pcnt = round(100- pcnt - neg_pcnt,2)
        print(f'at {count} / {NUM_ITEMS} : {pcnt} % zeros ,{pos_pcnt} % pos. , {neg_pcnt} % neg ')
    #------#
#-----#

def merge_and_save(_lora1 , _lora2 , _lora3, savefile_name, new_rank , new_alpha, resolution):
    lora = {}
    count = 0
    for key in _lora1:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = resolution*0.000001 # 1e-6

    #-------#
    for key in _lora1:
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        #if count<462:
        #    count = count + 2
        #    continue
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#

        # Setup
        delta_W = torch.matmul(_lora1[up]*0,_lora1[down]*0).to(device = device, dtype=torch.float32)
        tgt_shape = delta_W.shape
        N = delta_W.numel()
        delta_W = torch.zeros(N).to(device = device , dtype=torch.float32)
        #-----#

        #Positives
        Y = torch.zeros(3,N).to(device = device , dtype=torch.float32)
        Y[0] = torch.matmul(_lora1[up],_lora1[down]).flatten().to(device = device , dtype=torch.float32)
        Y[1] = torch.matmul(_lora2[up],_lora2[down]).flatten().to(device = device , dtype=torch.float32)
        Y[2] = torch.matmul(_lora3[up],_lora3[down]).flatten().to(device = device , dtype=torch.float32)
        Y[torch.abs(Y)<thresh] = 0 #Trim
        Y = torch.round(Y,decimals=6).t()
        num = torch.sum(Y>0,dim=1) + 0.001
        elect = torch.sum(Y<0,dim=1) + 0.001
        elect = (num>=elect)
        Y[Y<0] = 0
        Y = torch.sum(Y, dim=1).to(device = device , dtype=torch.float32)
        delta_W[elect] = torch.round((Y[elect]/num[elect]),decimals=6).to(device = device , dtype=torch.float32)
        #-----#

        #Negatives
        Y = torch.zeros(3,N).to(device = device , dtype=torch.float32)
        Y[0] = torch.matmul(_lora1[up],_lora1[down]).flatten().to(device = device , dtype=torch.float32)
        Y[1] = torch.matmul(_lora2[up],_lora2[down]).flatten().to(device = device , dtype=torch.float32)
        Y[2] = torch.matmul(_lora3[up],_lora3[down]).flatten().to(device = device , dtype=torch.float32)
        Y[torch.abs(Y)<thresh] = 0 #Trim
        Y = torch.round(Y,decimals=6).t()
        num = torch.sum(Y<0,dim=1) + 0.001  # <-- to prevent divide by 0
        elect = torch.sum(Y>0,dim=1) + 0.001
        elect = (elect<num)
        Y[Y>0] = 0
        Y = torch.sum(Y, dim=1).to(device = device , dtype=torch.float32)
        delta_W[elect] = torch.round(Y[elect]/num[elect],decimals=6).to(device = device , dtype=torch.float32)
        #----#

        # Free up memory prior to SVD
        delta_W = delta_W.unflatten(0,tgt_shape).to(device = device , dtype=torch.float32)
        delta_W = delta_W.clone().detach()
        Y = {}
        num = {}
        num = {}
        elect = {}
        #-----#

        # Run SVD (Single Value Decomposition)
        #to get the new lora_up and lora_down for delta_W
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        tmp['u'] = torch.matmul(tmp['u'], torch.diag(tmp['s']))
        tmp['Vh'] = tmp['Vh'].t()[: new_rank,:]
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = torch.round(tmp['u'],decimals=6).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(tmp['Vh'],decimals=6).to(device = device , dtype=torch.float32)
        #-------#

        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}')
        #----#
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#------#

new_rank = 32
new_alpha = math.floor(new_rank/2)
resolution = 200
name = 'yeero_euro_puff'
yeero = load_file('/content/drive/MyDrive/Saved from Chrome/yeero_100_r32_16alpha.safetensors')
euro = load_file('/content/drive/MyDrive/Saved from Chrome/euro_100_r32_16alpha.safetensors')
puff = load_file('/content/drive/MyDrive/Saved from Chrome/puff_200_r32_16alpha.safetensors')
savefile_name = f'{name}_{resolution}_r{new_rank}_a{new_alpha}.safetensors'

#tgt = load_file(f'/kaggle/input/flux-loras/{name}_{resolution}_r32_16alpha.safetensors')
for key in yeero:
    yeero[f'{key}'] = yeero[f'{key}'].to(device = device , dtype = torch.float32)
    euro[f'{key}'] = euro[f'{key}'].to(device = device , dtype = torch.float32)
    puff[f'{key}'] = puff[f'{key}'].to(device = device , dtype = torch.float32)
#-----#
print(f'for {name}.safetensors at scale = (rank/alpha) = 0.5')
merge_and_save(yeero , euro , puff, savefile_name, new_rank , new_alpha, resolution)


#Yeero + Scale + Puff
#filter_and_save(tgt , f'{name}_{resolution}_r{new_rank}_{new_alpha}alpha.safetensors' , new_rank , new_alpha, resolution)


for yeero_euro_puff.safetensors at scale = (rank/alpha) = 0.5
1 / 912
3 / 912
4 / 912
6 / 912
7 / 912
9 / 912
10 / 912
12 / 912
13 / 912
15 / 912
16 / 912
18 / 912
19 / 912
21 / 912
22 / 912
24 / 912
25 / 912
27 / 912
28 / 912
30 / 912
31 / 912
33 / 912
34 / 912
36 / 912
37 / 912
39 / 912
40 / 912
42 / 912
43 / 912
45 / 912
46 / 912
48 / 912
49 / 912
51 / 912
52 / 912
54 / 912
55 / 912
57 / 912
58 / 912
60 / 912
61 / 912
63 / 912
64 / 912
66 / 912
67 / 912
69 / 912
70 / 912
72 / 912
73 / 912
75 / 912
76 / 912
78 / 912
79 / 912
81 / 912
82 / 912
84 / 912
85 / 912
87 / 912
88 / 912
90 / 912
91 / 912
93 / 912
94 / 912
96 / 912
97 / 912
99 / 912
100 / 912
102 / 912
103 / 912
105 / 912
106 / 912
108 / 912
109 / 912
111 / 912
112 / 912
114 / 912
115 / 912
117 / 912
118 / 912
120 / 912
121 / 912
123 / 912
124 / 912
126 / 912
127 / 912
129 / 912
130 / 912
132 / 912
133 / 912
135 / 912
136 / 912
138 / 912
139 / 912
141 / 912
142 / 912
144 / 912
145 / 912
147 / 912
148 / 912
150 / 912
151 / 912


In [ ]:
from safetensors.torch import load_file, save_file
_puff = load_file('/content/drive/MyDrive/Saved from Chrome/pfbkFLUX.safetensors')
puff = {}

#alpha = 64
#rank = 64

# = > so scale = 1
#desired scale = 0.5
# so multiply matrices by 2 and set alpha to 32
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
for key in _puff:
  if f'{key}'.find('alpha')>-1:
    puff[f'{key}'] = torch.tensor(32).to(device=device , dtype = torch.float16)
    #print(puff[f'{key}'])
    continue
  puff[f'{key}'] = 2*_puff[f'{key}'].to(device=device , dtype = torch.float16)

  #print(puff[f'{key}'].shape)

save_file(puff, 'puff.safetensors')

In [ ]:
from safetensors.torch import load_file, save_file
_tongue = load_file('/content/drive/MyDrive/Saved from Chrome/tongue-flux-v2.1.safetensors')
tongue = {}
# Scale = 32/16 = 2
# Desired scale = 0.5  => multiply all matrices by 4 and set alpha to 8
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
for key in _tongue:
  if f'{key}'.find('alpha')>-1:
    tongue[f'{key}'] = torch.tensor(8).to(device=device , dtype = torch.float16)
    continue
  #-------#
  tongue[f'{key}'] = 4*_tongue[f'{key}'].to(device=device , dtype = torch.float16)
#-------#
save_file(tongue, 'tongue.safetensors')

In [ ]:


device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

_oily = load_file('/content/drive/MyDrive/Saved from Chrome/OiledSkin_FluxDev.safetensors')

star = load_file('/content/drive/MyDrive/Saved from Chrome/star_100_r32_16alpha.safetensors')
#A = vs , B = u
#lora_down = A , lora_up = B

oily = {}
for key in _oily:
  if not f'{key}'.find('_A.')>-1:continue
  A = f'{key}'
  B = f'{key}'.replace('_A.','_B.')
  down = f'{key}'.replace('_A.','_down.')
  up = f'{key}'.replace('_A.','_up.')
  #-----#
  oily[f'{up}'] = _oily[f'{B}'].to(device = device , dtype=torch.float16)
  oily[f'{down}'] = _oily[f'{A}'].to(device = device , dtype=torch.float16)
  #------#
  if not f'{key}'.find('to_k.')>-1:continue
  k = f'{key}'
  q = k.replace('to_k.','to_q.')
  v = k.replace('to_k.','to_v.')

print("---------OILY---------")
for key in oily:
  print(key)
  #if f'{key}'.find('alpha')>-1:print(key)

print("---------STAR---------")
for key in star:
  break
  print(key)

---------OILY---------
transformer.single_transformer_blocks.0.attn.to_k.lora_up.weight
transformer.single_transformer_blocks.0.attn.to_k.lora_down.weight
transformer.single_transformer_blocks.0.attn.to_q.lora_up.weight
transformer.single_transformer_blocks.0.attn.to_q.lora_down.weight
transformer.single_transformer_blocks.0.attn.to_v.lora_up.weight
transformer.single_transformer_blocks.0.attn.to_v.lora_down.weight
transformer.single_transformer_blocks.0.norm.linear.lora_up.weight
transformer.single_transformer_blocks.0.norm.linear.lora_down.weight
transformer.single_transformer_blocks.0.proj_mlp.lora_up.weight
transformer.single_transformer_blocks.0.proj_mlp.lora_down.weight
transformer.single_transformer_blocks.0.proj_out.lora_up.weight
transformer.single_transformer_blocks.0.proj_out.lora_down.weight
transformer.single_transformer_blocks.1.attn.to_k.lora_up.weight
transformer.single_transformer_blocks.1.attn.to_k.lora_down.weight
transformer.single_transformer_blocks.1.attn.to_q.lor

In [ ]:
down = 'lora_unet_double_blocks_0_img_attn_qkv.lora_down.weight'
up = 'lora_unet_double_blocks_0_img_attn_qkv.lora_up.weight'
tgt = star
print("STAR")
print(tgt[f'{up}'].shape)
#print(torch.matmul(tgt[f'{up}'],tgt[f'{down}']).shape)

down = 'transformer.transformer_blocks.0.attn.to_k.lora_down.weight'
up = 'transformer.transformer_blocks.0.attn.to_k.lora_up.weight'
tgt = oily
print("VS. OILY")
print(tgt[f'{up}'].shape)
#print(torch.matmul(tgt[f'{up}'],tgt[f'{down}']).shape)


STAR
torch.Size([9216, 32])
VS. OILY
torch.Size([3072, 32])


In [ ]:
for key in oily:
  print(oily[f'{key}'].shape)

torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([9216, 32])
torch.Size([32, 3072])
torch.Size([12288, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 15360])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([9216, 32])
torch.Size([32, 3072])
torch.Size([12288, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 15360])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([9216, 32])
torch.Size([32, 3072])
torch.Size([12288, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 15360])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([3072, 32])
torch.Size([32, 3072])
torch.Size([9216, 32])
torch

In [ ]:

import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
def _filter(tgt , pcnt, largest):
    num_topk = math.floor(tgt.numel()*(pcnt/100))
    y = tgt.flatten().to(device = device , dtype=torch.float32)
    values,indices = torch.topk( y ,  num_topk , largest=largest)
    _values,_indices = torch.topk( -y , num_topk , largest=largest)
    y = y*0
    y[indices] = 1
    y[_indices] = 1
    y = y.unflatten(0,tgt.shape).to(device = device , dtype=torch.float32)
    return torch.mul(tgt,y)

#----#

# For pcnt = 30 , 'filter_and_save'  will keep all top 30 % values
#, and the lowest (negative) 30% values for each layer delta_W in this lora
# Then save the new filtered lora as a .safetensor file
def filter_and_save(_lora , savefile_name, new_rank , new_alpha, thresh):
    lora = {}
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = resolution*0.000001 # 1e-6
    #-------#
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        #---#
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.zeros(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 1
        y[indices[values<-thresh]] = 1
        y = y.unflatten(0,delta_W.shape).to(device = device , dtype=torch.float32)
        delta_W = torch.mul(delta_W,y).to(device = device , dtype=torch.float32)
        #------#
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        #-------#
        tmp['u'] = torch.round(torch.matmul(tmp['u'], torch.diag(tmp['s'])),decimals=6)
        tmp['Vh'] = torch.round(tmp['Vh'].t()[: new_rank,:],decimals=6)
        #-------#
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = tmp['u'].to(device = device , dtype=torch.float32)
        lora[down] = tmp['Vh'].to(device = device , dtype=torch.float32)
        #-------#
        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}')
    #-------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in _lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#--------#


new_rank = 32
new_alpha = new_rank/2
resolution = 100
star = load_file('/kaggle/input/flux-loras/yeero.safetensors')
for key in star:
    star[f'{key}'] = star[f'{key}'].to(device = device , dtype = torch.float32)

filter_and_save(star , f'yeero_{resolution}_r{new_rank}_{new_alpha}alpha.safetensors' , new_rank , new_alpha, resolution)

#pcnt = 30
#new_rank = 6
#filter_and_save(yeero , f'yeero_topk{pcnt}_r{new_rank}.safetensors' , pcnt , new_rank)
#filter_and_save(euro , f'euro_topk{pcnt}_r{new_rank}.safetensors' , pcnt , new_rank)
#filter_and_save(star , f'star_topk{pcnt}_r{new_rank}.safetensors' , pcnt , new_rank)


In [ ]:
cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi_style.safetensors')

In [ ]:
#cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi_style.safetensors')
doll = load_file('/content/drive/MyDrive/Saved from Chrome/dolls.safetensors')
euro = load_file('/content/drive/MyDrive/Saved from Chrome/euro.safetensors')
scale = load_file('/content/drive/MyDrive/Saved from Chrome/scale.safetensors')
cgi = load_file('/content/drive/MyDrive/Saved from Chrome/cgi.safetensors')
guns = load_file('/content/drive/MyDrive/Saved from Chrome/guns.safetensors')
iris = load_file('/content/drive/MyDrive/Saved from Chrome/iris.safetensors')

In [ ]:
for key in doll:
  doll[f'{key}'] = doll[f'{key}'].to(dtype=torch.float16)
  euro[f'{key}'] = euro[f'{key}'].to(dtype=torch.float16)
  scale[f'{key}'] = scale[f'{key}'].to(dtype=torch.float16)

In [ ]:
import torch
import torch.nn as nn
#define metric for similarity
tgt_dim = torch.Size([64, 3072])
cos0 = nn.CosineSimilarity(dim=1)
cos = nn.CosineSimilarity(dim=1)


def sim(tgt , ref ,key):
  return torch.sum(torch.abs(cos(tgt, ref[f'{key}'])))  + torch.sum(torch.abs(cos0(tgt, ref[f'{key}'])))
#-----#

from torch import linalg as LA

LA.matrix_norm
def rand_search(A , B , key , iters):
  tgt_norm = (LA.matrix_norm(A[f'{key}']) + LA.matrix_norm(B[f'{key}']))/2
  tgt_avg = (A[f'{key}'] + B[f'{key}'])/2

  max_sim = (sim(tgt_avg , A , key) + sim(tgt_avg , B , key))
  cand = tgt_avg

  for iter in range(iters):
    rand = torch.ones(tgt_dim)*(-0.5)  + torch.rand(tgt_dim)
    rand = rand  * (tgt_norm/LA.matrix_norm(rand))
    #rand = (rand + tgt_avg)/2
    #rand = rand  * (tgt_norm/LA.matrix_norm(rand))

    tmp = sim(rand,A, key) + sim(rand , B, key)
    if (tmp > max_sim):
      max_sim = tmp
      cand = rand
      print('found!')
      break
  #------#
  print('returning')
  return cand  , max_sim
#-----#

In [ ]:
cand , max_sim = rand_search(cgi , iris , 'lora_unet_double_blocks_0_img_attn_proj.lora_down.weight' , 1000)
print(sim(cand , iris , key))
print(sim(cand , cgi , key))

returning
tensor(91.1875, dtype=torch.float16)
tensor(90.2500, dtype=torch.float16)


In [ ]:
(torch.rand(1).to(dtype=torch.float16)*3).item()

0.2138671875

In [ ]:
torch.rand(1).to(dtype=torch.float16)*10

tensor([6.8555], dtype=torch.float16)

In [ ]:
import torch
import torch.nn as nn
#define metric for similarity
tgt_dim = torch.Size([64, 3072])
cos0 = nn.CosineSimilarity(dim=0)



cos = nn.CosineSimilarity(dim=1)


def sim(tgt , ref ,key):
  return torch.sum(torch.abs(cos(tgt, ref[f'{key}'])))  + torch.sum(torch.abs(cos0(tgt, ref[f'{key}'])))
#-----#

7.715576171875

In [ ]:
from safetensors.torch import load_file , save_file
import torch
import torch.nn as nn
from torch import linalg as LA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#define metric for similarity
cos0 = nn.CosineSimilarity(dim=0).to(device)
final_score = 0
highest_score = 0
w_cgi = 1
w_doll = 2
w_euro = 2
w_guns = 1
w_iris = 2
w_scale = 1

w_noise = 0.00001 * (w_cgi + w_doll + w_euro  + w_guns + w_iris + w_scale)
fixed_noise = {}

#for key in doll:
#  fixed_noise[f'{key}'] = torch.zeros(doll[f'{key}'].shape).to(device = device , dtype=torch.float16)
#------#
#w_offset = 0* (w1+w2+w3)
#_w_offset = 0

W =  (w_cgi + w_doll + w_euro  + w_guns + w_iris + w_scale + w_noise)*torch.ones(1).to(device = device,dtype=torch.float16)

SCALE = 0.0001
one = torch.ones(1).to(dtype=torch.float16).to(device)

for attempt in range(1000):
  print(f'attempt no : {attempt+1} ')
  merge = load_file('/content/drive/MyDrive/Saved from Chrome/dolls.safetensors')
  for key in doll:
    tgt_dim = doll[f'{key}'].shape
    if tgt_dim == torch.Size([]): continue
    r_cgi = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_cgi
    r_doll = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_doll
    r_euro = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_euro
    r_guns = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_guns
    r_iris = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_iris
    r_scale = torch.rand(1).to(device = device,dtype=torch.float16).item()*w_scale
    #------#
    noise = torch.rand(tgt_dim).to(device = device,dtype=torch.float16)
    noise_norm = LA.matrix_norm(noise).to(device = device,dtype=torch.float16).item()
    noise = (w_noise/noise_norm)*noise.to(device = device,dtype=torch.float16)
    #-----#
    merge[f'{key}'] = r_cgi * cgi[f'{key}'] #overwrite
    merge[f'{key}'] = merge[f'{key}'] + r_doll * doll[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_euro * euro[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_guns * guns[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_iris * iris[f'{key}']
    merge[f'{key}'] = merge[f'{key}'] + r_scale * scale[f'{key}']
    merge[f'{key}'] = ((merge[f'{key}'] + noise)/W).to(device = device,dtype=torch.float16)
  #-------#
  score = torch.zeros(1).to(device = device, dtype=torch.float32)
  #----#
  NUM_ITERS = 10
  for iter in range(NUM_ITERS):
    for key in doll:
      tgt_dim = doll[f'{key}'].shape
      if tgt_dim == torch.Size([]): continue
      vec = torch.rand(tgt_dim[0]).to(device = device,dtype=torch.float16)
      cgi_out = torch.matmul(vec , cgi[f'{key}']).to(device = device,dtype=torch.float16)
      doll_out = torch.matmul(vec , doll[f'{key}']).to(device = device,dtype=torch.float16)
      euro_out = torch.matmul(vec , euro[f'{key}']).to(device = device,dtype=torch.float16)
      guns_out = torch.matmul(vec , guns[f'{key}']).to(device = device,dtype=torch.float16)
      iris_out = torch.matmul(vec , iris[f'{key}']).to(device = device,dtype=torch.float16)
      scale_out = torch.matmul(vec , scale[f'{key}']).to(device = device,dtype=torch.float16)
      merge_out = torch.matmul(vec , merge[f'{key}']).to(device = device,dtype=torch.float16)
      #-------#
      sim_value_cgi = torch.abs(cos0(cgi_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_doll = torch.abs(cos0(doll_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_euro = torch.abs(cos0(euro_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_guns = torch.abs(cos0(guns_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_iris = torch.abs(cos0(iris_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      sim_value_scale = torch.abs(cos0(scale_out , merge_out)).to(device = device,dtype=torch.float32)*SCALE
      score = score  + SCALE*(sim_value_cgi + 2*sim_value_doll +  2*sim_value_euro + sim_value_guns + 2*sim_value_iris + sim_value_scale)/9  #<--- This score can be anything at all
      #----#
  #-----#

  final_score = (1000/(NUM_ITERS * SCALE))*score.to(device = 'cpu' , dtype=torch.float32).item()
  if (final_score>highest_score) :
    highest_score = final_score
    print('new highscore!')
    print(f'score : {final_score} pts')
    #------#
    save_file(merge , 'all_merge_R4.safetensors')
  #------#

print(f'------------')
print(f'Final score : {highest_score} pts')


#all R1 23.190992578747682

#all R2 23.333244826062582

#all R3 23.34471355425194

#all R4 23.402637452818453

attempt no : 1 
new highscore!
score : 23.264414267032407 pts
attempt no : 2 
attempt no : 3 
attempt no : 4 
new highscore!
score : 23.29399467271287 pts
attempt no : 5 
attempt no : 6 
attempt no : 7 
attempt no : 8 
attempt no : 9 
attempt no : 10 
attempt no : 11 
new highscore!
score : 23.362628780887462 pts
attempt no : 12 
attempt no : 13 
attempt no : 14 
attempt no : 15 
attempt no : 16 
attempt no : 17 
attempt no : 18 
attempt no : 19 
attempt no : 20 
attempt no : 21 
attempt no : 22 
attempt no : 23 
new highscore!
score : 23.37011210329365 pts
attempt no : 24 
attempt no : 25 
attempt no : 26 
attempt no : 27 
attempt no : 28 
attempt no : 29 
attempt no : 30 
attempt no : 31 
attempt no : 32 
attempt no : 33 
attempt no : 34 
new highscore!
score : 23.402637452818453 pts
attempt no : 35 
attempt no : 36 
attempt no : 37 
attempt no : 38 
attempt no : 39 
attempt no : 40 
attempt no : 41 
attempt no : 42 
attempt no : 43 
attempt no : 44 
attempt no : 45 
attempt no : 46 

KeyboardInterrupt: 

In [ ]:
    for key in doll:
      if final_score<38.5: break
      _w_offset = w_offset
      W =  (w1+w2+w3 + w_noise + _w_offset)*torch.ones(1).to(device = device,dtype=torch.float16)
      tgt_dim = doll[f'{key}'].shape
      if tgt_dim == torch.Size([]): continue
      fixed_noise[f'{key}'] = fixed_noise[f'{key}'] + merge[f'{key}']
      fixed_noise[f'{key}'] = (fixed_noise[f'{key}'] * (w_offset*torch.ones(1).to(device = device,dtype=torch.float16)/LA.matrix_norm(fixed_noise[f'{key}']))).to(device = device,dtype=torch.float16)

In [ ]:
  vec = torch.rand(tgt_dim[0]).to(dtype=torch.float16)
  same = torch.abs(cos0(vec ,vec))

In [ ]:
same

tensor(1., dtype=torch.float16)

In [ ]:
torch.ones(1).to(dtype=torch.float16)

tensor([1.], dtype=torch.float16)

score : 45.8125 pts


In [ ]:
%cd /content/
save_file(merge , 'doll_euro_scale_R_merge.safetensors')

In [ ]:
test = torch.rand(tgt_dim)
vec = torch.rand(tgt_dim[0])

In [ ]:
tgt_dim[0]

9216

In [ ]:
(torch.matmul(vec,test)).shape

torch.Size([64])

In [ ]:
tgt_dim = torch.Size([64, 3072])
cosa = nn.CosineSimilarity(dim=0)
cos_dim1 = nn.CosineSimilarity(dim=1)

for key in cgi:
  if not cgi[f'{key}'].shape == torch.Size([64, 3072]): continue
  print(f'{key} : ')
  print(torch.sum(torch.abs(cos_dim1(cgi[f'{key}'] , iris[f'{key}']))))

lora_unet_double_blocks_0_img_attn_proj.lora_down.weight : 
tensor(1.6982, dtype=torch.float16)
lora_unet_double_blocks_0_img_attn_qkv.lora_down.weight : 
tensor(1.8145, dtype=torch.float16)
lora_unet_double_blocks_0_img_mlp_0.lora_down.weight : 
tensor(1.6309, dtype=torch.float16)
lora_unet_double_blocks_0_img_mod_lin.lora_down.weight : 
tensor(2.6211, dtype=torch.float16)
lora_unet_double_blocks_0_txt_attn_proj.lora_down.weight : 
tensor(2.3203, dtype=torch.float16)
lora_unet_double_blocks_0_txt_attn_qkv.lora_down.weight : 
tensor(2.3027, dtype=torch.float16)
lora_unet_double_blocks_0_txt_mlp_0.lora_down.weight : 
tensor(2.5898, dtype=torch.float16)
lora_unet_double_blocks_0_txt_mod_lin.lora_down.weight : 
tensor(2.7402, dtype=torch.float16)
lora_unet_double_blocks_10_img_attn_proj.lora_down.weight : 
tensor(2.0410, dtype=torch.float16)
lora_unet_double_blocks_10_img_attn_qkv.lora_down.weight : 
tensor(1.3350, dtype=torch.float16)
lora_unet_double_blocks_10_img_mlp_0.lora_down.weight

<---- Upload your civiai trained .safetensor file to Google Colab before running the next cell



In [ ]:
civiai_lora = '' # @param {type:'string' ,placeholder:'ex. civitai_trained_e19.safetensors'}
tensor_art_filename = '' # @param {type:'string' ,placeholder:'ex. e19.safetensors'}
%cd /content/
tgt = load_file(f'{civiai_lora}')
for key in tgt:
  tgt[f'{key}'] = tgt[f'{key}'].to(dtype=torch.float16)
%cd /content/
save_file(tgt , f'{tensor_art_filename}')

Download the new .safetensor file to your device.

Downloading from CoLab Notebook will seemingly do nothing for ~5min. Then the file will download , so be patient.

For faster/more consistent downloads , download your .safetensor file from your Google Drive